In [6]:
import spacy
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn import feature_extraction, linear_model, model_selection, preprocessing, svm
import seaborn as sns
import matplotlib.pyplot as plt
import re
import string
import nltk

In [90]:
!python3 -m spacy download en_core_web_lg

2022-11-23 16:22:46.490748: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-11-23 16:22:46.490776: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
RuntimeError: module compiled against API version 0xe but this version of numpy is 0xd
     |████████████████████████████████| 587.7 MB 2.5 kB/s eta 0:00:014   |▉                               | 15.6 MB 2.7 MB/s eta 0:03:32     |█                               | 17.4 MB 2.7 MB/s eta 0:03:32     |█▎                              | 23.5 MB 3.2 MB/s eta 0:02:57     |█▍                              | 25.5 MB 3.7 MB/s eta 0:02:34     |█▍                              | 26.2 MB 3.7 MB/s eta 0:02:34     |██▏                             | 39.0 MB 3.2 MB/s eta 0:02:53     |█████▎                          | 96.2 MB 4

✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_lg')


In [89]:
nlp = spacy.load('en_core_web_lg')

OSError: [E050] Can't find model 'en_core_web_lg'. It doesn't seem to be a Python package or a valid path to a data directory.

In [10]:
import pandas as pd
df = pd.read_csv('/home/siddhant/NEU/IR_CS6200/imdb_data.csv')
df

docid                                    title    year  \
0     599986                                 The Wash  2001.0   
1      97099                      Caught in the Draft  1941.0   
2     186674                         Eyes of the Soul  1919.0   
3     567084                           The J2 Project  2002.0   
4     381575                             Muno no hito  1991.0   
...      ...                                      ...     ...   
9995  141713                              Desert Moon  1994.0   
9996  404061                    O Casamento de Louise  2001.0   
9997  267864  Invasion of the Buddy Snatcher: Bad Dad  2009.0   
9998  271350                                   Izydi!  1991.0   
9999  584806                         The Puzzle Place  1994.0   

                  type                        colors  \
0                movie                     ['Color']   
1                movie           ['Black and White']   
2                movie           ['Black and White']   
3        DirectToVideo                     ['Color']   
4                movie                     ['Color']   
...                ...                           ...   
9995     DirectToVideo                     ['Color']   
9996             movie                     ['Color']   
9997     DirectToVideo                     ['Color']   
9998             movie  ['Black and White', 'Color']   
9999  TelevisionSeries                     ['Color']   

                                genres       languages         countries  \
0                           ['Comedy']     ['English']           ['USA']   
1         ['War', 'Comedy', 'Romance']     ['English']           ['USA']   
2                 ['Drama', 'Romance']              []           ['USA']   
3                            ['Short']     ['English']           ['USA']   
4                  ['Drama', 'Comedy']    ['Japanese']         ['Japan']   
...                                ...             ...               ...   
9995  ['Comedy', 'Adventure', 'Adult']     ['English']           ['USA']   
9996             ['Comedy', 'Romance']  ['Portuguese']        ['Brazil']   
9997               ['Short', 'Comedy']     ['English']        ['Canada']   
9998               ['Drama', 'Comedy']     ['Russian']  ['Soviet Union']   
9999                                []     ['English']           ['USA']   

                                           releasedates  \
0     {'South Africa': '11 October 2002', 'UK': '9 A...   
1     {'Sweden': '6 October 1941', 'France': '14 May...   
2                              {'USA': '20 April 1919'}   
3                             {'USA': '31 August 2004'}   
4     {'Netherlands': '5 August 1993', 'Japan': '2 N...   
...                                                 ...   
9995                     {'Spain': '27 September 1995'}   
9996                         {'Brazil': '13 June 2001'}   
9997                                                 {}   
9998  {'Germany': '16 February 1992', 'Canada': '11 ...   
9999           {'UK': '1995', 'USA': '17 January 1995'}   

                                    directors  \
0                                ['Pooh, DJ']   
1                       ['Butler, David (I)']   
2                         ['Chautard, Emile']   
3                           ['Horwitz, Alex']   
4                         ['Takenaka, Naoto']   
...                                       ...   
9995                      ['Steelberg, Greg']   
9996                      ['De Paula, Betse']   
9997    ['Amo, Michael', 'Moore, Craig (IX)']   
9998                    ['Astrakhan, Dmitri']   
9999  ['Martin, Hugh (III)', 'Trbovich, Tom']   

                                              producers  \
0     ['Chavous, Donna', 'Chavous, Donna', 'Samuels,...   
1                                 ['DeSylva, Buddy G.']   
2                                                    []   
3                                 ['Lesin, Sara Elisa']   
4                                ['Okuyama, Kaz

In [26]:
doc = []
doc_noun = []

def get_column_tokenized(column_name):
    for i in range(len(df[column_name])):
        doc.append(list(nlp(df[column_name][i])))
        temp = nlp(df[column_name][i])
        spacy.displacy.render(temp, style = "ent")
        doc_noun.append(list(temp.noun_chunks))
    #print(doc)
    print(doc_noun)

In [27]:
get_column_tokenized('title')

[[The Wash], [the Draft], [Eyes, the Soul], [The J2 Project], [Muno], [Hot Dog], [A Deadly Compromise], [VH1 News Presents, Plastic Surgery Obsession], [Lazzarella], [], [The Trespassers], [Perry Rhodan - Operation Eastside], [], [Savage Skies], [Baseball Girls], [Judgment Day], [Swingers], [The Prize], [Le jour du combat], [Young Warriors], [The Leather Girls], [The Green Hornet], [Sons, Daughters], [The Last Shift], [Sailor Siren Song], [Miss Lonely Hearts], [Sons o], [It], [Cannonball], [Il comandante], [Lizzie Borden, an Axe], [Fool, Love], [Bed], [Classroom Discipline], [Champion], [A Study, Terror], [Jet Pink], [Terror Tract], [Benji], [The Mikado], [], [Last Chance Saloon], [Sawblade], [Primetime Glick], [Plastic Wolves], [Aap Ki Khatir], [Cries Unheard, The Donna Yaklich Story], [Sanmunui seunggaek], [May Beetle], [Hombre mirando al sudeste], [Elias, The Little Rescue Boat], [Maniac Bloodbath], [Il papa buono], [Les distractions], [Grace, My Heart], [The 4th Beast, Mask, the An

In [15]:
doc = nlp(df.title[0])
spacy.displacy.render(doc, style = "ent")
doc_nouns = list(doc.noun_chunks)
print(doc_nouns)

/home/siddhant/anaconda3/lib/python3.7/site-packages/spacy/displacy/__init__.py:206: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)


AttributeError: 'spacy.tokens.doc.Doc' object has no attribute 'noun'

In [13]:
[(i, i.ent_type_, i.is_stop) for j in range(len(doc)) for i in doc[j] ]

[(The, '', True),
 (Wash, '', False),
 (Caught, '', False),
 (in, '', True),
 (the, '', True),
 (Draft, 'ORG', False),
 (Eyes, '', False),
 (of, '', True),
 (the, '', True),
 (Soul, '', False),
 (The, '', True),
 (J2, 'CARDINAL', False),
 (Project, '', False),
 (Muno, 'NORP', False),
 (no, '', True),
 (hito, '', False),
 (Hot, '', False),
 (Dog, '', False),
 (A, '', True),
 (Deadly, '', False),
 (Compromise, '', False),
 (VH1, 'ORG', False),
 (News, 'ORG', False),
 (Presents, 'ORG', False),
 (:, 'ORG', False),
 (Plastic, 'ORG', False),
 (Surgery, 'ORG', False),
 (Obsession, '', False),
 (Lazzarella, '', False),
 (Go, '', True),
 (Further, '', True),
 (The, '', True),
 (Trespassers, '', False),
 (Perry, 'PERSON', False),
 (Rhodan, 'PERSON', False),
 (-, 'PERSON', False),
 (Operation, 'PERSON', False),
 (Eastside, 'PERSON', False),
 (Covered, '', False),
 (Savage, '', False),
 (Skies, '', False),
 (Baseball, '', False),
 (Girls, '', False),
 (Judgment, 'DATE', False),
 (Day, 'DATE', Fals

English movie shot in USA in 1993


In [97]:
nlp.get_pipe('ner').labels

('CARDINAL',
 'DATE',
 'EVENT',
 'FAC',
 'GPE',
 'LANGUAGE',
 'LAW',
 'LOC',
 'MONEY',
 'NORP',
 'ORDINAL',
 'ORG',
 'PERCENT',
 'PERSON',
 'PRODUCT',
 'QUANTITY',
 'TIME',
 'WORK_OF_ART')

In [105]:

def filter_result(li):
    result = df

    for i in li:
        if i.ent_type_.lower() == 'language':
            result = result[result.languages.apply(lambda x: i.text in x)]
        elif i.ent_type_.lower() == 'gpe':
            result = result[result.countries.apply(lambda x: i.text in x)]
        elif i.ent_type_.lower() == 'date':
            result = result.loc[df['year'] == float(i.text)]
    return result

In [106]:
query = "Movies shot in 1993"
li = nlp(query)
spacy.displacy.render(li, style = "ent")
print(li)
result = filter_result(li)

Movies shot in 1993


In [107]:
result

docid                       title    year              type     colors  \
65    564317               The Hidden II  1993.0             movie  ['Color']   
132   521649                Sunes sommar  1993.0             movie  ['Color']   
309   125667               Dancing Queen  1993.0   TelevisionMovie  ['Color']   
320   130191                Dave's World  1993.0  TelevisionSeries  ['Color']   
335    20253                       Aadmi  1993.0             movie  ['Color']   
...      ...                         ...     ...               ...        ...   
9787  416191              Os Salteadores  1993.0             movie         []   
9839  474089                      Sainik  1993.0             movie  ['Color']   
9844  307569     La corsa dell'innocente  1993.0             movie  ['Color']   
9857  328592  Legend of the Buffalo Clan  1993.0             movie  ['Color']   
9908  618714        Trois couleurs: Bleu  1993.0             movie  ['Color']   

                                       genres  \
65              ['Horror', 'Crime', 'Sci-Fi']   
132                      ['Family', 'Comedy']   
309                     ['Comedy', 'Romance']   
320                                ['Comedy']   
335   ['Drama', 'Romance', 'Action', 'Crime']   
...                                       ...   
9787                   ['Short', 'Animation']   
9839                     ['Family', 'Action']   
9844                                ['Drama']   
9857                 ['Documentary', 'Short']   
9908                                ['Drama']   

                             languages                            countries  \
65                         ['English']                              ['USA']   
132             ['Swedish', 'English']                           ['Sweden']   
309                        ['English']                               ['UK']   
320                        ['English']                              ['USA']   
335                          ['Hindi']                            ['India']   
...                                ...                                  ...   
9787                                []                         ['Portugal']   
9839                         ['Hindi']                            ['India']   
9844                       ['Italian']                  ['France', 'Italy']   
9857                       ['English']                              ['USA']   
9908  ['French', 'Romanian', 'Polish']  ['France', 'Poland', 'Switzerland']   

                                           releasedates  \
65    {'Japan': '6 September 1993', 'Hungary': '21 A...   
132   {'Sweden': '25 December 1993', 'Germany': '24 ...   
309    {'UK': '3 June 1993', 'Finland': '22 July 2003'}   
320                        {'USA': '27 September 1995'}   
335                         {'India': '3 October 1993'}   
...                                                 ...   
9787                                                 {}   
9839                     {'India': '10 September 1993'}   
9844  {'Portugal': '6 June 1996', 'UK': '18 February...   
9857                                                 {}   
9908  {'Sweden': '17 December 1993', 'Argentina': '3...   

                                              directors  \
65                                    ['Pinsker, Seth']   
132                               ['Apelgren, Stephan']   
309                                      ['Hamm, Nick']   
320   ['Day, Linda (I)', 'Dielhenn, Art', 'Drake, Ji...   
335                                ['Khan, Arshad (I)']   
...                                                 ...   
9787                                     ['Feijó, Abi']   
9839                               ['Bharti, Sikander']   
9844                                  ['Carlei, Carlo']   
9857                            ['Mitchell, Wayne (I)']   
9908                          ['Kieslowski, Krzysztof']   

                                              producers  \
65    ['Ordesky, Ma